In [20]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import display
import altair as alt
# Enable VegaFusion data transformer
alt.data_transformers.enable('vegafusion')
# Disable the default row limit data transformer
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('vegafusion')

In [2]:
df_sp = pd.read_pickle('data/SP500.pkl')
df_nifty = pd.read_pickle('data/NIFTY50.pkl')
df_ftse = pd.read_pickle('data/FTSE100.pkl')

In [ ]:
df_sp.sample(5)

In [ ]:
def EDA(df):
    

In [ ]:
df_sp.dtypes

In [ ]:
df_sp.Close.plot()

In [ ]:
df.Volume.plot()

In [ ]:
dataframes = [df_sp, df_nifty, df_ftse]

for df in dataframes:
    df['daily_return'] = df['Close'].pct_change().fillna(0)
    df['cumulative_return'] = (1 + df['daily_return']).cumprod().fillna(1)
    print(df.index.name + ' Summary')
    display(df.describe())
    print('------------------------------------------------------------------------------------------------------'+'\n')

In [ ]:
df_sp['daily_return'].plot()

In [ ]:
df_sp['Close'].resample('M').mean().plot()


In [ ]:
df_sp['Close'].resample('Y').mean().plot()

In [ ]:
df_corr = pd.concat([df_sp['Close'], df_nifty['Close'], df_ftse['Close']], axis=1)

In [ ]:
df_corr.columns = ['SP500', 'NIFTY50', 'FTSE100']

In [ ]:
sns.pairplot(df_corr)

In [ ]:
sns.heatmap(df_corr.corr(), annot=True)


In [25]:

def EDA(df):
    # Ensure the 'Date' column is in datetime format
    df.index = pd.to_datetime(df.index)
    
    # Calculate daily return and cumulative return
    df['daily_return'] = df['Close'].pct_change().fillna(0)
    df['cumulative_return'] = (1 + df['daily_return']).cumprod().fillna(1)
    
    # Create a selection interval
    brush = alt.selection_interval(encodings=['x'])
    
    # Candlestick chart for OHLC data
    base = alt.Chart(df.reset_index()).encode(
        x='Date:T',
        tooltip=['Date:T', 'Open:Q', 'High:Q', 'Low:Q', 'Close:Q']
    ).properties(
        width=800,
        height=300,
        title='Candlestick Chart of Closing Prices'
    ).add_selection(
        brush
    ).interactive()
    
    rule = base.mark_rule().encode(
        y='Low:Q',
        y2='High:Q'
    )
    
    bar = base.mark_bar().encode(
        y='Open:Q',
        y2='Close:Q',
        color=alt.condition("datum.Open <= datum.Close",
                            alt.value("#06982d"),  # Green for increasing
                            alt.value("#ae1325"))  # Red for decreasing
    )
    
    candlestick_chart = rule + bar
    
    # Line plot for volume
    volume = alt.Chart(df.reset_index()).mark_line().encode(
        x='Date:T',
        y='Volume:Q',
        tooltip=['Date:T', 'Volume:Q']
    ).properties(
        width=800,
        height=200,
        title='Volume over Time'
    ).transform_filter(
        brush
    )
    
    # Line plot for daily returns
    daily_return = alt.Chart(df.reset_index()).mark_line().encode(
        x='Date:T',
        y='daily_return:Q',
        tooltip=['Date:T', 'daily_return:Q']
    ).properties(
        width=800,
        height=200,
        title='Daily Returns'
    ).transform_filter(
        brush
    )
    
    # Line plot for cumulative returns
    cumulative_return = alt.Chart(df.reset_index()).mark_line().encode(
        x='Date:T',
        y='cumulative_return:Q',
        tooltip=['Date:T', 'cumulative_return:Q']
    ).properties(
        width=800,
        height=200,
        title='Cumulative Returns'
    ).transform_filter(
        brush
    )
    
    # Monthly resampled mean closing prices
    df_monthly = df['Close'].resample('M').mean().reset_index()
    monthly_close = alt.Chart(df_monthly).mark_line().encode(
        x='Date:T',
        y='Close:Q',
        tooltip=['Date:T', 'Close:Q']
    ).properties(
        width=800,
        height=200,
        title='Monthly Average Closing Prices'
    ).transform_filter(
        brush
    )
    
    # Yearly resampled mean closing prices
    df_yearly = df['Close'].resample('Y').mean().reset_index()
    yearly_close = alt.Chart(df_yearly).mark_line().encode(
        x='Date:T',
        y='Close:Q',
        tooltip=['Date:T', 'Close:Q']
    ).properties(
        width=800,
        height=200,
        title='Yearly Average Closing Prices'
    ).transform_filter(
        brush
    )
    
    # Combine all charts into a single dashboard with an overall title
    dashboard = alt.vconcat(
        candlestick_chart,
        volume,
        daily_return,
        cumulative_return,
        monthly_close,
        yearly_close
    ).configure_axis(
        labelFontSize=12,
        titleFontSize=14
    ).configure_title(
        fontSize=16
    ).properties(
        title='Exploratory Data Analysis Dashboard'
    )
    
    return dashboard

In [26]:
EDA(df_sp)

/Users/philipnj/anaconda3/lib/python3.11/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'add_selection' is deprecated. Use 'add_params' instead.
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)


alt.VConcatChart(...)